In [2]:
# Learning Practice 2 for the University of Tulsa's QM-7063 Data Mining Course
# Dimension Reduction
# Professor: Dr. Abdulrashid, Spring 2023
# Noah L. Schrick - 1492657

import heapq
from collections import defaultdict

import pandas as pd
import matplotlib.pylab as plt
from mlxtend.frequent_patterns import apriori
from mlxtend.frequent_patterns import association_rules

from surprise import Dataset, Reader, KNNBasic
from surprise.model_selection import train_test_split


# Problem 14.1
An analyst at a subscription-based satellite radio company has been given a sample of data from their customer database, with the goal of finding groups of customers who are associated with one another. The data consist of company data, together with purchased  demographic data that are mapped to the company data (see Table 14.13). The analyst decides to apply association rules to learn more about the associations between customers. Comment on this approach.

This is a good approach for exploring associative relationships between customers. Since there is company data mixed with demographic data, the association rules can yield better results and demonstrate better associations since purchases can be examined with respect to age, location, number of dependents, and any other demographic data available.

# Problem 14.3
We again consider the data in CourseTopics.csv describing course purchases at Statistics.com (see Problem 14.2 and data sample in Table 14.14). We want to provide a course recommendation to a student who purchased the Regression and Forecast courses. Apply user-based collaborative filtering to the data. You will get a Null matrix. Explain why this happens.

In [28]:
## Read in Course Topics data
courses_df = pd.read_csv('Coursetopics.csv')

# Convert to format usable for surprise similarities
courses_df['Index'] = range(1, len(courses_df) + 1)
course_melt = courses_df.melt(id_vars =['Index'], value_vars =['Intro', 'DataMining', 'Survey', 'Cat Data', 'Regression', 'Forecast', 'DOE', 'SW'], 
        var_name ='Course', value_name ='Taken')


reader = Reader(rating_scale=(0, 1))
data = Dataset.load_from_df(course_melt[['Index', 'Course', 'Taken']], reader)
trainset = data.build_full_trainset()

# NOTE: The following will error. This is expected and part of the question. Explanation in the corresponding answer.
sim_options = {'name': 'cosine', 'user_based': True}  # compute cosine similarities between users
algo = KNNBasic(sim_options=sim_options)
algo.fit(trainset)
#pred = algo.predict(str(823519), str(30), r_ui=4, verbose=True)

Computing the cosine similarity matrix...


ZeroDivisionError: float division

The provided dataset is composed of Boolean values for "have taken" or "have not taken" various courses. The dataset represents "have not taken" with a 0, and "taken" with a 1. The dataset is considered a sparse matrix, since each user has only taken a few of the listed courses. Due to the sparsity, when computing the cosine between users, many computations involve comparing a user's "not taken" course to another user's "not taken" course. This leads to difficulties with the cosine computation since the denominator will be zero, causing a float division error. This can be remedied by using "NULL" values, which are supported in the surprise package.

# Problem 14.4
The data shown in Table 14.15 and the output in Table 14.16 are based on a subset of a dataset on cosmetic purchases (Cosmetics.csv) at a large chain drugstore. The store wants to analyze associations among purchases of these items for purposes of point-of-sale display, guidance to sales personnel in promoting cross-sales, and guidance for piloting an eventual time-of-purchase electronic recommender
system to boost cross-sales. Consider first only the data shown in Table 14.15, given in binary matrix form.
    a. Select several values in the matrix and explain their meaning.
    b. Consider the results of the association rules analysis shown in Table 14.16.
        i. For the first row, explain the “confidence” output and how it is calculated.
        ii. For the first row, explain the “support” output and how it is calculated.
        iii. For the first row, explain the “lift” and how it is calculated.
        iv. For the first row, explain the rule that is represented there in words.
    c. Now, use the complete dataset on the cosmetics purchases (in the file Cosmetics.csv). Using Python, apply association rules to these data (for apriori use min_support=0.1 and use_colnames=True, for association_rules use default parameters).
        i. Interpret the first three rules in the output in words.
        ii. Reviewing the first couple of dozen rules, comment on their redundancy and how you would assess their utility.